In [1]:
from tqdm.auto import tqdm as auto_tqdm
import tqdm

tqdm.tqdm = auto_tqdm

In [2]:
from typing import List, Optional
from dataclasses import dataclass, field

@dataclass
class ScriptArguments:
    """
    The name of the Casual LM model we wish to fine with SFTTrainer
    """

    model_name: Optional[str] = field(default="facebook/opt-350m", metadata={"help": "the model name"})
    dataset_name: Optional[str] = field(
        default="timdettmers/openassistant-guanaco", metadata={"help": "the dataset name"}
    )
    dataset_text_field: Optional[str] = field(default="text", metadata={"help": "the text field of the dataset"})
    report_to: Optional[str] = field(default="none", metadata={"help": "use 'wandb' to log with wandb"})
    learning_rate: Optional[float] = field(default=1.41e-5, metadata={"help": "the learning rate"})
    batch_size: Optional[int] = field(default=64, metadata={"help": "the batch size"})
    seq_length: Optional[int] = field(default=512, metadata={"help": "Input sequence length"})
    gradient_accumulation_steps: Optional[int] = field(
        default=1, metadata={"help": "the number of gradient accumulation steps"}
    )
    load_in_8bit: Optional[bool] = field(default=False, metadata={"help": "load the model in 8 bits precision"})
    load_in_4bit: Optional[bool] = field(default=False, metadata={"help": "load the model in 4 bits precision"})
    use_peft: Optional[bool] = field(default=False, metadata={"help": "Wether to use PEFT or not to train adapters"})
    trust_remote_code: Optional[bool] = field(default=False, metadata={"help": "Enable `trust_remote_code`"})
    output_dir: Optional[str] = field(default="output", metadata={"help": "the output directory"})
    peft_lora_r: Optional[int] = field(default=64, metadata={"help": "the r parameter of the LoRA adapters"})
    peft_lora_alpha: Optional[int] = field(default=16, metadata={"help": "the alpha parameter of the LoRA adapters"})
    logging_steps: Optional[int] = field(default=1, metadata={"help": "the number of logging steps"})
    use_auth_token: Optional[bool] = field(default=False, metadata={"help": "Use HF auth token to access the model"})
    num_train_epochs: Optional[int] = field(default=3, metadata={"help": "the number of training epochs"})
    max_steps: Optional[int] = field(default=-1, metadata={"help": "the number of training steps"})
    save_steps: Optional[int] = field(
        default=100, metadata={"help": "Number of updates steps before two checkpoint saves"}
    )
    save_total_limit: Optional[int] = field(default=10, metadata={"help": "Limits total number of checkpoints."})
    push_to_hub: Optional[bool] = field(default=False, metadata={"help": "Push the model to HF Hub"})
    fp16: Optional[bool] = field(default=False, metadata={"help": "Whether to activate fp16 mixed precision"})
    bf16: Optional[bool] = field(default=False, metadata={"help": "Whether to activate bf16 mixed precision"})
    gradient_checkpointing: Optional[bool] = field(
        default=False, metadata={"help": "Whether to use gradient checkpointing or no"}
    )
    gradient_checkpointing_kwargs: Optional[dict] = field(
        default=None,
        metadata={
            "help": "key word arguments to be passed along `torch.utils.checkpoint.checkpoint` method - e.g. `use_reentrant=False`"
        },
    )
    hub_model_id: Optional[str] = field(default=None, metadata={"help": "The name of the model on HF Hub"})
    mixed_precision: Optional[str] = field(default="bf16", metadata={"help": "Mixed precision training"})
    target_modules: Optional[List[str]] = field(default=None, metadata={"help": "Target modules for LoRA adapters"})


In [3]:
# accelerate launch --config_file examples/accelerate_configs/multi_gpu.yaml --num_processes=1 \
# 	examples/scripts/sft.py \
# 	--model_name mistralai/Mixtral-8x7B-Instruct-v0.1 \
# 	--dataset_name trl-lib/ultrachat_200k_chatml \
# 	--batch_size 2 \
# 	--gradient_accumulation_steps 1 \
# 	--learning_rate 2e-4 \
# 	--save_steps 200_000 \
# 	--use_peft \
# 	--peft_lora_r 16 --peft_lora_alpha 32 \
# 	--target_modules q_proj k_proj v_proj o_proj \
# 	--load_in_4bit

In [2]:
import torch
from accelerate import Accelerator
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, TrainingArguments
from peft import LoraConfig
from trl import is_xpu_available

# sft.py script version 0.7.10

device_map = (
    {"": f"xpu:{Accelerator().local_process_index}"}
        if is_xpu_available()
        else {"": Accelerator().local_process_index}
)

torch_dtype = torch.bfloat16

quantization_config = BitsAndBytesConfig(
    load_in_4bit=True
)

training_args = TrainingArguments(
    output_dir = './output1',
    per_device_train_batch_size = 2,
    gradient_accumulation_steps = 1,
    learning_rate = 2e-4,
    logging_steps = 1,
    num_train_epochs = 3,
    max_steps = -1,
    #report_to = 'wandb',
    save_steps = 200_000,
    save_total_limit = 10,
    push_to_hub = False,
    hub_model_id = None,
    gradient_checkpointing = False,
    gradient_checkpointing_kwargs = dict(use_reentrant=False),
    fp16 = False,
    bf16 = False,
)

peft_config = LoraConfig(
    r = 16,
    lora_alpha = 32,
    bias = "none",
    task_type = "CAUSAL_LM",
    target_modules = ['q_proj', 'k_proj', 'v_proj', 'o_proj']
)

model_name = 'mistralai/Mixtral-8x7B-Instruct-v0.1'
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    quantization_config = quantization_config,
    device_map = device_map,
    trust_remote_code = False,
    torch_dtype = torch_dtype
)

tokenizer = AutoTokenizer.from_pretrained(model_name, use_fast=True)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = 'right'

Loading checkpoint shards:   0%|          | 0/19 [00:00<?, ?it/s]

In [5]:
import wandb, os
wandb.login()

wandb_project = "mixtral-select-finetune"
if len(wandb_project) > 0:
    os.environ["WANDB_PROJECT"] = wandb_project

wandb: Currently logged in as: antonvo (northern-light). Use `wandb login --relogin` to force relogin


In [6]:
from datasets import load_dataset, DatasetDict, concatenate_datasets
import pandas as pd

# Filenames of your CSV files
filenames = ['./select-1.csv', './select-2.csv', './select-3.csv']

# Load datasets and split each
split_datasets = {'train': [], 'validation': []}

for filename in filenames:
    # Load the CSV file as a Dataset
    dataset = load_dataset('csv', data_files=filename, split='train')

    # Split the dataset into training and validation
    split = dataset.train_test_split(test_size=0.2, seed=42)
    
    # Append the split datasets to the corresponding lists
    split_datasets['train'].append(split['train'])
    split_datasets['validation'].append(split['test'])

# Concatenate the datasets for training and validation
train_dataset = concatenate_datasets(split_datasets['train'])
eval_dataset = concatenate_datasets(split_datasets['validation'])

In [9]:
from trl import SFTTrainer

trainer = SFTTrainer(
    model = model,
    args = training_args,
    max_seq_length = 512, #32 * 1024,
    train_dataset = train_dataset,
    eval_dataset = eval_dataset,
    dataset_text_field = 'text',
    peft_config = peft_config,
    tokenizer = tokenizer
)

Map:   0%|          | 0/24000 [00:00<?, ? examples/s]

Map:   0%|          | 0/6000 [00:00<?, ? examples/s]

In [ ]:
trainer.train()
trainer.save_model('./output1')

In [14]:
from peft import PeftModel

ft_model = PeftModel.from_pretrained(model, "./output1")

def generate_response(prompt):
    encoded_input = tokenizer(prompt, return_tensors="pt", add_special_tokens=True)
    model_inputs = encoded_input.to('cuda')

    generated_ids = ft_model.generate(**model_inputs,
                                 max_new_tokens=150,
                                 do_sample=True,
                                 pad_token_id=tokenizer.eos_token_id)
    decoded_output = tokenizer.batch_decode(generated_ids)
    return decoded_output[0]

In [15]:
prompt = "[INST] Hey, what's up? [/INST]"
generate_response(prompt)

'<s> [INST] Hey, what\'s up? [/INST] Hello! I\'m doing well, thank you for asking. How about you? 🙂\n\nAs for the topic, since it\'s Easter Sunday today, I thought it would be appropriate to share a song about the holiday. This one is called "Jesus and Rosemary" and it\'s a traditional Irish tune featuring the accordion, tin whistle, and bodhrán instruments. The lyrics tell the story of Jesus, his mother Mary, and the resurrection that Easter commemorates. Here they are in case you want to follow along:\n\nUpon a golden Sunday, As morning broke so soon, Rosemary\'s arms were thrown around a tree, As if to claim it\'s tune.'

In [21]:
model.config.to_json_file('config.json')